In [1]:
import os
import requests
import json
import gzip
import pandas as pd
import glob

In [2]:
companies = ['LLY', 'AAPL', 'BEP']
params = {'function': 'TIME_SERIES_INTRADAY',
          'symbol': 'BEP',
          'interval': '1min',
          'month': '2025-01',
          'outputsize': 'full',
          'extended_hours': 'false',
          'apikey': os.environ["API_KEY"]
          }

In [46]:
yyyy = '2025'

In [25]:
mm=['01', '02', '03', '04', '05', '06', '07', '08', '09', '10', '11', '12']

In [47]:
mm=['01', '02', '03', '04', '05', '06', '07', '08', '09']

In [48]:
for m in mm:
    params['month']=yyyy+"-"+m
    url = "https://www.alphavantage.co/query?"
    for key, val in params.items():
        url+=key
        url+='='
        url+=val
        url+='&'
    url = url[:-1]
    print(url)
    r = requests.get(url)
    data = r.json()
    print(data)
    df = pd.DataFrame.from_dict(data['Time Series (1min)'], orient='index')
    df = df.sort_index()
    # print(df)
    df.to_csv(params['symbol'] + params['month'] + '.csv.gz', compression='gzip')



https://www.alphavantage.co/query?function=TIME_SERIES_INTRADAY&symbol=BEP&interval=1min&month=2025-01&outputsize=full&extended_hours=false&apikey=953WQPZROCIH6YLX
{'Meta Data': {'1. Information': 'Intraday (1min) open, high, low, close prices and volume', '2. Symbol': 'BEP', '3. Last Refreshed': '2025-01-31 15:59:00', '4. Interval': '1min', '5. Output Size': 'Full size', '6. Time Zone': 'US/Eastern'}, 'Time Series (1min)': {'2025-01-31 15:59:00': {'1. open': '20.9133', '2. high': '20.9229', '3. low': '20.8752', '4. close': '20.9038', '5. volume': '24750'}, '2025-01-31 15:58:00': {'1. open': '20.8561', '2. high': '20.9181', '3. low': '20.8561', '4. close': '20.9133', '5. volume': '31032'}, '2025-01-31 15:57:00': {'1. open': '20.8656', '2. high': '20.8943', '3. low': '20.8561', '4. close': '20.8561', '5. volume': '20870'}, '2025-01-31 15:56:00': {'1. open': '20.8847', '2. high': '20.8943', '3. low': '20.8561', '4. close': '20.8847', '5. volume': '11582'}, '2025-01-31 15:55:00': {'1. ope

In [ ]:
data = pd.read_csv("LLY2024-01.csv.gz")
data

In [17]:
csv_files = glob.glob(os.path.join(os.getcwd(), f"*{params['symbol']}*.csv.gz"))

combined_df = pd.concat((pd.read_csv(f) for f in csv_files), ignore_index=True)
combined_df.to_csv(f"{params['symbol']}_combined.csv.gz", compression='gzip', index=False)

In [5]:
metrics = ["EARNINGS", "INCOME_STATEMENT", "BALANCE_SHEET", "CASH_FLOW", "SHARES_OUTSTANDING"]
stocks = ["AAPL", "BEP", "LLY"]

In [6]:
supplemental_info = {}
for i in stocks:
    supplemental_info[i] = {}
    for j in metrics:
        url = f'https://www.alphavantage.co/query?function={j}&symbol={i}&apikey={os.environ["API_KEY"]}'
        r = requests.get(url)
        data = r.json()
        supplemental_info[i][j] = data


In [41]:
supplemental_info['AAPL']['BALANCE_SHEET']

{'symbol': 'AAPL',
 'annualReports': [{'fiscalDateEnding': '2025-09-30',
   'reportedCurrency': 'None',
   'totalAssets': '359241000000',
   'totalCurrentAssets': '147957000000',
   'cashAndCashEquivalentsAtCarryingValue': '35934000000',
   'cashAndShortTermInvestments': '35934000000',
   'inventory': '5718000000',
   'currentNetReceivables': '72957000000',
   'totalNonCurrentAssets': '211284000000',
   'propertyPlantEquipment': 'None',
   'accumulatedDepreciationAmortizationPPE': 'None',
   'intangibleAssets': 'None',
   'intangibleAssetsExcludingGoodwill': 'None',
   'goodwill': 'None',
   'investments': 'None',
   'longTermInvestments': 'None',
   'shortTermInvestments': '18763000000',
   'otherCurrentAssets': '14585000000',
   'otherNonCurrentAssets': 'None',
   'totalLiabilities': '285508000000',
   'totalCurrentLiabilities': '165631000000',
   'currentAccountsPayable': '69860000000',
   'deferredRevenue': 'None',
   'currentDebt': 'None',
   'shortTermDebt': '7979000000',
   'tot

In [35]:
quaterly_earnings_date = []
for stock in stocks:
    for i in supplemental_info['AAPL']['EARNINGS']['quarterlyEarnings']:
        date = pd.to_datetime(i['reportedDate'])
        if date.year>2019:
            quaterly_earnings_date.append({
                "Quarterly Earnings": i['reportedDate'],
                "Surprise": i['surprise'], 
                "Surprise Percentage": i['surprisePercentage']
                })
    df = pd.DataFrame(quaterly_earnings_date)
    df.to_csv(f"{stock}_quarterly_earnings.csv")

In [48]:
for stock in stocks:
    for i in range(1,len(metrics)):
        print(metrics[i])
        print(supplemental_info[stock][metrics[i]])
        if metrics[i] == "SHARES_OUTSTANDING":
            df = pd.DataFrame(supplemental_info[stock][metrics[i]]['data'])
        else:
            df = pd.DataFrame(supplemental_info[stock][metrics[i]]['annualReports'])
        df.to_csv(f"{stock}_{metrics[i]}.csv.gz", compression="gzip")

INCOME_STATEMENT
{'symbol': 'AAPL', 'annualReports': [{'fiscalDateEnding': '2025-09-30', 'reportedCurrency': 'None', 'grossProfit': '195201000000', 'totalRevenue': '416161000000', 'costOfRevenue': '220960000000', 'costofGoodsAndServicesSold': '220960000000', 'operatingIncome': '133050000000', 'sellingGeneralAndAdministrative': 'None', 'researchAndDevelopment': '34550000000', 'operatingExpenses': '62151000000', 'investmentIncomeNet': 'None', 'netInterestIncome': 'None', 'interestIncome': 'None', 'interestExpense': 'None', 'nonInterestIncome': 'None', 'otherNonOperatingIncome': 'None', 'depreciation': 'None', 'depreciationAndAmortization': '11698000000', 'incomeBeforeTax': '132729000000', 'incomeTaxExpense': '20719000000', 'interestAndDebtExpense': 'None', 'netIncomeFromContinuingOperations': 'None', 'comprehensiveIncomeNetOfTax': 'None', 'ebit': '132729000000', 'ebitda': '144427000000', 'netIncome': '112010000000'}, {'fiscalDateEnding': '2024-09-30', 'reportedCurrency': 'USD', 'grossPro

In [10]:
file_path = 'calendar.txt'
cal_dict = {}
try:
    with open(file_path, 'r') as file:
        for line_number, line in enumerate(file, 1):
            value = line.strip()
            if value[0]!='2':
                key=value
                cal_dict[key] = []
            else:
                yy=value[:4]
                mm=value[4:6]
                dd=value[6:]
                cal_dict[key].append(yy+'-'+mm+'-'+dd)
            print(f"Line {line_number}: {line.strip()}")
except FileNotFoundError:
    print(f"Error: The file '{file_path}' was not found.")
except Exception as e:
    print(f"An error occurred: {e}")

Line 1: OptionExpiry
Line 2: 20200117
Line 3: 20200221
Line 4: 20200417
Line 5: 20200515
Line 6: 20200717
Line 7: 20200821
Line 8: 20201016
Line 9: 20201120
Line 10: 20210115
Line 11: 20210219
Line 12: 20210416
Line 13: 20210521
Line 14: 20210716
Line 15: 20210820
Line 16: 20211015
Line 17: 20211119
Line 18: 20220121
Line 19: 20220218
Line 20: 20220414
Line 21: 20220520
Line 22: 20220715
Line 23: 20220819
Line 24: 20221021
Line 25: 20221118
Line 26: 20230120
Line 27: 20230217
Line 28: 20230421
Line 29: 20230519
Line 30: 20230721
Line 31: 20230818
Line 32: 20231020
Line 33: 20231117
Line 34: 20240119
Line 35: 20240216
Line 36: 20240419
Line 37: 20240517
Line 38: 20240719
Line 39: 20240816
Line 40: 20241018
Line 41: 20241115
Line 42: 20250117
Line 43: 20250221
Line 44: 20250417
Line 45: 20250516
Line 46: 20250718
Line 47: 20250815
Line 48: 20251017
Line 49: FOMC
Line 50: 20200129
Line 51: 20200318
Line 52: 20200429
Line 53: 20200610
Line 54: 20200729
Line 55: 20200916
Line 56: 20201105
L

In [22]:
for key in list(cal_dict.keys()):
    df = pd.DataFrame(cal_dict[key])
    df.to_csv(f"{key}_calendar_dates.csv.gz", compression="gzip")
